In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore')
import seaborn as sns
import json
import math

In [2]:
import math
import numpy as np
class calculator():
    def __init__(self,lat1,lat2,lon1,lon2):
        self.lat1 = lat1 # start lat
        self.lat2 = lat2 # end lat
        self.lon1 = lon1 # start lon
        self.lon2 = lon2 # end lon
        self.x1 = self.lat1*math.pi/180
        self.x2 = self.lat2*math.pi/180
        self.dx = (self.lat2-lat1) * math.pi/180 # theta_dev
        self.dy = (self.lon2-lon1) * math.pi/180 # lambda_dev
        self.R = 6378.1*1000 # meter
        
    def distance(self):  
        a = math.sin(self.dx/2)**2 + math.cos(self.x1)*math.cos(self.x2)*math.sin(self.dy/2)*math.sin(self.dy/2)
        c = 2*math.atan2(np.sqrt(a),np.sqrt(1-a))
        d = self.R*c
        return d # meter
    def bearing(self):
        y = math.sin(self.dy) * math.cos(self.x2)
        x = math.cos(self.x1)*math.sin(self.x2)-math.sin(self.x1)*math.cos(self.x2)*math.cos(self.dy)
        seta = math.atan2(y,x)
        brng = (seta*180/math.pi+360)%360
        return brng # radian to degree
    def points(self,d): 
        lat1 = math.radians(self.lat1) # radian
        lon1 = math.radians(self.lon1) # radian
        brng = math.radians(self.bearing()) # radian
        lat2 = math.asin( math.sin(lat1)*math.cos(d/self.R) +math.cos(lat1)*math.sin(d/self.R)*math.cos(brng))
        lon2 = lon1 + math.atan2(math.sin(brng)*math.sin(d/self.R)*math.cos(lat1),math.cos(d/self.R)\
                                 -math.sin(lat1)*math.sin(lat2))
        lat2 = math.degrees(lat2)
        lon2 = math.degrees(lon2)
        return lat2,lon2

In [3]:
file = 'tram/트램선로.geojson'
geo = json.load(open(file,encoding='utf-8'))

In [4]:
feat = geo['features']
lat=[]
lon=[]
for i in range(len(feat)):
    x = feat[i]['geometry']['coordinates']
    for j in range(len(x)):
        lat.append(x[j][1])
        lon.append(x[j][0])

In [5]:
point = pd.DataFrame(columns = ['latitude','longitude'])
point['latitude'] = lat
point['longitude'] = lon

In [6]:
import folium
m = folium.Map(location = [36.44,127.24],tiles='OpenStreetMap',zoom_start = 10)
for lat, lon,idx in zip(point['latitude'], point['longitude'],range(len(point))):
    folium.CircleMarker([lat, lon],
                        radius=5,
                        color='red',
                        popup = '{},{}'.format(lat,lon),
                        fill_color='red',
                        fill_opacity=0.7 ).add_to(m)

In [7]:
m

In [8]:
dis = []
angle = []
for i in range(len(point)-1):
    if i == 0:
        dis.append(np.nan)
        angle.append(np.nan)
    x1 = point['latitude'][i]
    y1 = point['longitude'][i]
    x2 = point['latitude'][i+1]
    y2 = point['longitude'][i+1]
    cal=calculator(x1,x2,y1,y2)
    dis.append(cal.distance())
    angle.append(cal.bearing())
point['distance'] = dis
point['bearing'] = angle

In [9]:
feat = geo['features']
x1 = feat[0]['geometry']['coordinates']
x2 = feat[1]['geometry']['coordinates']
x3 = feat[2]['geometry']['coordinates']

In [10]:
x1_df = pd.DataFrame(columns=['lat','lon'])
lat1=[]
lon1=[]
for i in x1:
    lat1.append(i[1])
    lon1.append(i[0])
x1_df['lat'] = lat1
x1_df['lon'] = lon1

x2_df = pd.DataFrame(columns=['lat','lon'])
lat2=[]
lon2=[]
for i in x2:
    lat2.append(i[1])
    lon2.append(i[0])
x2_df['lat'] = lat2
x2_df['lon'] = lon2

x3_df = pd.DataFrame(columns=['lat','lon'])
lat3=[]
lon3=[]
for i in x3:
    lat3.append(i[1])
    lon3.append(i[0])
x3_df['lat'] = lat3
x3_df['lon'] = lon3

# x1 (곡선)

In [12]:
dis = []
ang=[]
for i in range(len(x1_df)-1):
    if i == 0:
        dis.append(np.nan)
        ang.append(np.nan)
    x1 = x1_df['lat'][i]
    y1 = x1_df['lon'][i]
    x2 = x1_df['lat'][i+1]
    y2 = x1_df['lon'][i+1]
    cal=calculator(x1,x2,y1,y2)
    dis.append(cal.distance())
    ang.append(cal.bearing())
x1_df['distance'] = dis
x1_df['angle'] = ang
x1_df.fillna(0,inplace=True)

In [13]:
x1_df

lat         lon  distance       angle
0   36.638751  127.305672  0.000000    0.000000
1   36.638783  127.305736  6.735741   58.072129
2   36.638786  127.305743  0.708862   61.893197
3   36.638791  127.305753  1.052459   58.072138
4   36.638796  127.305765  1.207781   62.558647
5   36.638800  127.305776  1.078748   65.620997
6   36.638810  127.305798  2.258516   60.469617
7   36.638813  127.305806  0.788775   64.951426
8   36.638814  127.305812  0.547381   78.266122
9   36.638819  127.305834  2.042425   74.185937
10  36.638825  127.305876  3.810588   79.905139
11  36.638829  127.305943  6.001231   85.744875
12  36.638828  127.305955  1.077649   95.929102
13  36.638823  127.305982  2.475134  102.995483
14  36.638811  127.306016  3.317807  113.742263
15  36.638799  127.306047  3.074409  115.753377
16  36.638796  127.306052  0.557670  126.787084
17  36.638770  127.306095  4.809324  126.999489
18  36.638767  127.306100  0.557670  126.787074
19  36.638736  127.306135  4.656454  137.824943
20  36.638700  127.306163  4.723899  148.031701

In [14]:
lat = [36.638751]
lon = [127.305672]
cal = calculator(x1_df['lat'][0],x1_df['lat'][2],x1_df['lon'][0],x1_df['lon'][2])
for i in range(1,int(x1_df['distance'][1])+1):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
# 0-2 까지 7.4 // 7미터에서 끊기

In [15]:
cal = calculator(lat[-1],x1_df['lat'][3],lon[-1],x1_df['lon'][3])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
# 2-3

In [16]:
cal = calculator(lat[-1],x1_df['lat'][4],lon[-1],x1_df['lon'][4])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#3-4

In [17]:
cal = calculator(lat[-1],x1_df['lat'][5],lon[-1],x1_df['lon'][5])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#4-5

In [18]:
cal = calculator(lat[-1],x1_df['lat'][6],lon[-1],x1_df['lon'][6])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#5-6

In [19]:
cal = calculator(lat[-1],x1_df['lat'][8],lon[-1],x1_df['lon'][8])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#6-8

In [20]:
cal = calculator(lat[-1],x1_df['lat'][9],lon[-1],x1_df['lon'][9])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#8-9

In [21]:
cal = calculator(lat[-1],x1_df['lat'][10],lon[-1],x1_df['lon'][10])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#9-10

In [22]:
cal = calculator(lat[-1],x1_df['lat'][11],lon[-1],x1_df['lon'][11])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#10-11

In [23]:
cal = calculator(lat[-1],x1_df['lat'][12],lon[-1],x1_df['lon'][12])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#11-12

In [24]:
cal = calculator(lat[-1],x1_df['lat'][13],lon[-1],x1_df['lon'][13])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#12-13

In [25]:
cal = calculator(lat[-1],x1_df['lat'][14],lon[-1],x1_df['lon'][14])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#13-14

In [26]:
cal = calculator(lat[-1],x1_df['lat'][15],lon[-1],x1_df['lon'][15])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#14-15

In [27]:
cal = calculator(lat[-1],x1_df['lat'][17],lon[-1],x1_df['lon'][17])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#15-17

In [28]:
cal = calculator(lat[-1],x1_df['lat'][19],lon[-1],x1_df['lon'][19])
for i in range(1,int(cal.distance()+1)):
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])
#17-19

In [29]:
cal = calculator(lat[-1],x1_df['lat'][20],lon[-1],x1_df['lon'][20])
for i in range(1,int(cal.distance()+2)): # 하나 넘어가게
    lat.append(cal.points(i)[0])
    lon.append(cal.points(i)[1])

In [30]:
df = pd.DataFrame(columns=['lat','lon'])
df['lat'] = lat
df['lon'] = lon

In [31]:
# df.to_excel('C:/Users/CVAI/Downloads/kym/geo_final/x1_points.xlsx',index=False)

# x1-x2 직선 라인

In [32]:
cal = calculator(lat[-1],x2_df['lat'][0],lon[-1],x2_df['lon'][0])
lat2=[]
lon2=[]
for i in range(1,int(cal.distance())+1):
    lat2.append(cal.points(i)[0])
    lon2.append(cal.points(i)[1])


In [33]:
# df = pd.DataFrame(columns=['lat','lon'])
# df['lat'] = lat2
# df['lon'] = lon2
# df.to_excel('C:/Users/CVAI/Downloads/kym/geo_final/x1_x2.xlsx',index=False)

# x2-x2 직선라인

In [60]:
tmp = pd.read_excel('geo_final/x1_x2.xlsx')


In [61]:
cal = calculator(tmp['lat'][len(tmp)-1],x2_df['lat'][13],tmp['lon'][len(tmp)-1],x2_df['lon'][13])
cal.distance()
lat3 = []
lon3 = []
for i in range(1,int(cal.distance())+2): # 하나 넘어가게
    lat3.append(cal.points(i)[0])
    lon3.append(cal.points(i)[1])

In [62]:
# df = pd.DataFrame(columns=['lat','lon'])
# df['lat'] = lat3
# df['lon'] = lon3
# df.to_excel('C:/Users/CVAI/Downloads/kym/geo_final/x2_straight_points.xlsx',index=False)

# x2-x3

In [63]:
x3_df1 = x3_df.iloc[:9].reset_index(drop=True)
x3_df2 = x3_df.iloc[9:].reset_index(drop=True)

In [64]:
x3_df2

lat         lon
0  36.630424  127.315372
1  36.630179  127.315593
2  36.630018  127.315773

In [65]:
cal = calculator(lat3[-1],x3_df2['lat'][0],lon3[-1],x3_df2['lon'][0])
lat4 = []
lon4 = []
for i in range(1,int(cal.distance())+2): # 하나 넘어가게
    lat4.append(cal.points(i)[0])
    lon4.append(cal.points(i)[1])

In [66]:
# df = pd.DataFrame(columns=['lat','lon'])
# df['lat'] = lat4
# df['lon'] = lon4
# df.to_excel('C:/Users/CVAI/Downloads/kym/geo_final/x2-x3.xlsx',index=False)

# x3_final

In [67]:
cal = calculator(lat4[-1],x3_df2['lat'][1],lon4[-1],x3_df2['lon'][1])
lat5 = []
lon5 = []
for i in range(1,int(cal.distance())+1):
    lat5.append(cal.points(i)[0])
    lon5.append(cal.points(i)[1])

In [68]:
cal = calculator(lat5[-1],x3_df2['lat'][2],lon5[-1],x3_df2['lon'][2])
for i in range(1,int(cal.distance())+2): # 하나 넘어가게
    lat5.append(cal.points(i)[0])
    lon5.append(cal.points(i)[1])

In [69]:
m = folium.Map(location = [36.44,127.24],tiles='OpenStreetMap',zoom_start = 10)
for i,j in zip(lat5,lon5):
    folium.CircleMarker([i,j],radius=1).add_to(m)
m

In [70]:
# df = pd.DataFrame(columns=['lat','lon'])
# df['lat'] = lat5
# df['lon'] = lon5
# df.to_excel('C:/Users/CVAI/Downloads/kym/geo_final/x3_final.xlsx',index=False)

# x2_curve

In [71]:
dis = []
ang=[]
for i in range(len(x2_df)-1):
    if i == 0:
        dis.append(np.nan)
        ang.append(np.nan)
    x1 = x2_df['lat'][i]
    y1 = x2_df['lon'][i]
    x2 = x2_df['lat'][i+1]
    y2 = x2_df['lon'][i+1]
    cal=calculator(x1,x2,y1,y2)
    dis.append(cal.distance())
    ang.append(cal.bearing())
x2_df['distance'] = dis
x2_df['angle'] = ang
x2_df.fillna(0,inplace=True)
x2_df

lat         lon   distance       angle
0   36.633536  127.311909   0.000000    0.000000
1   36.633431  127.311980  13.298379  151.514755
2   36.633322  127.312097  16.014501  139.259444
3   36.633179  127.312255  21.274666  138.438260
4   36.633056  127.312392  18.364415  138.209262
5   36.632919  127.312545  20.478907  138.133460
6   36.632783  127.312701  20.576703  137.370802
7   36.632646  127.312855  20.538666  137.947778
8   36.632582  127.312924   9.420722  139.134552
9   36.632516  127.313006  10.374813  135.085505
10  36.632504  127.313024   2.090446  129.718406
11  36.632487  127.313048   2.859678  131.434233
12  36.632457  127.313093   5.226115  129.718384
13  36.632441  127.313128   3.598316  119.668547

In [72]:
tmp = pd.read_excel('geo_final/x1_x2.xlsx')
cal = calculator(tmp['lat'][len(tmp)-1],x2_df['lat'][1],tmp['lon'][len(tmp)-1],x2_df['lon'][1])
lat6 = []
lon6 = []
for i in range(1,int(cal.distance())+1):
    lat6.append(cal.points(i)[0])
    lon6.append(cal.points(i)[1])

In [73]:
for i in range(2,13):
    cal = calculator(lat6[-1],x2_df['lat'][i],lon6[-1],x2_df['lon'][i])
    for j in range(1,int(cal.distance())+1):
        lat6.append(cal.points(j)[0])
        lon6.append(cal.points(j)[1])

In [74]:
cal = calculator(lat6[-1],x2_df['lat'][13],lon6[-1],x2_df['lon'][13])
for i in range(1,int(cal.distance())+2): # 하나 넘어서
    lat6.append(cal.points(i)[0])
    lon6.append(cal.points(i)[1])

In [75]:
# df = pd.DataFrame(columns=['lat','lon'])
# df['lat'] = lat6
# df['lon'] = lon6
# df.to_excel('C:/Users/CVAI/Downloads/kym/geo_final/x2_curve.xlsx',index=False)

# sub_start

In [50]:
dis = []
ang=[]
for i in range(len(x3_df1)-1):
    if i == 0:
        dis.append(np.nan)
        ang.append(np.nan)
    x1 = x3_df1['lat'][i]
    y1 = x3_df1['lon'][i]
    x2 = x3_df1['lat'][i+1]
    y2 = x3_df1['lon'][i+1]
    cal=calculator(x1,x2,y1,y2)
    dis.append(cal.distance())
    ang.append(cal.bearing())
x3_df1['distance'] = dis
x3_df1['angle'] = ang
x3_df1.fillna(0,inplace=True)
x3_df1

lat         lon  distance       angle
0  36.638694  127.305842  0.000000    0.000000
1  36.638719  127.305912  6.844035   66.006838
2  36.638730  127.305949  3.524532   69.670146
3  36.638735  127.305987  3.439638   80.687571
4  36.638733  127.306029  3.758201   93.396206
5  36.638729  127.306068  3.511971   97.284003
6  36.638718  127.306119  4.717218  105.045278
7  36.638700  127.306163  4.411557  117.013608
8  36.638700  127.306163  0.000000    0.000000

In [51]:
x3_df1.drop(index=8,axis=0,inplace=True)

In [52]:
x3_df1

lat         lon  distance       angle
0  36.638694  127.305842  0.000000    0.000000
1  36.638719  127.305912  6.844035   66.006838
2  36.638730  127.305949  3.524532   69.670146
3  36.638735  127.305987  3.439638   80.687571
4  36.638733  127.306029  3.758201   93.396206
5  36.638729  127.306068  3.511971   97.284003
6  36.638718  127.306119  4.717218  105.045278
7  36.638700  127.306163  4.411557  117.013608

In [53]:
cal = calculator(x3_df1['lat'][0],x3_df1['lat'][1],x3_df1['lon'][0],x3_df1['lon'][1])
lat7 = []
lon7 = []
for i in range(1,int(cal.distance())+1):
    lat7.append(cal.points(i)[0])
    lon7.append(cal.points(i)[1])

In [54]:
for i in range(1,8):
    cal = calculator(lat7[-1],x3_df1['lat'][i],lon7[-1],x3_df1['lon'][i])
    for j in range(1,int(cal.distance()+1)):
        lat7.append(cal.points(j)[0])
        lon7.append(cal.points(j)[1])

In [55]:
# df = pd.DataFrame(columns=['lat','lon'])
# df['lat'] = lat7
# df['lon'] = lon7
# df.to_excel('C:/Users/CVAI/Downloads/kym/geo_final/sub_start.xlsx',index=False)

# 절대->상대
 - 좌표 계산기 돌리기

# Visualization

In [76]:
import os
ls = os.listdir('geo_final/')
data= pd.DataFrame()
for i in ls:
    df = pd.read_excel('geo_final/{}'.format(i))
    data= pd.concat([data,df])
data

lat         lon             X             Y
0   36.638698  127.305852  6.086350e+06  4.651116e+06
1   36.638701  127.305862  6.086350e+06  4.651118e+06
2   36.638705  127.305873  6.086350e+06  4.651120e+06
3   36.638709  127.305883  6.086350e+06  4.651121e+06
4   36.638712  127.305893  6.086350e+06  4.651123e+06
..        ...         ...           ...           ...
53  36.630040  127.315749  6.085004e+06  4.652759e+06
54  36.630033  127.315756  6.085003e+06  4.652760e+06
55  36.630026  127.315764  6.085002e+06  4.652761e+06
56  36.630020  127.315771  6.085001e+06  4.652763e+06
57  36.630013  127.315778  6.085000e+06  4.652764e+06

[1541 rows x 4 columns]

In [77]:
m = folium.Map(location = [36.44,127.24],tiles='OpenStreetMap',zoom_start = 10)
for i,j in zip(data['lat'],data['lon']):
    folium.CircleMarker([i,j],radius=1).add_to(m)
m

In [78]:
# data.to_excel('geo_final/inter.xlsx',index=False)

# 절대 -> 상대
- 원점에서 뺴기

In [85]:
data.reset_index(drop=True,inplace=True)

In [86]:
for i,j in enumerate(data['lat']):
    if j == 36.638751:
        print(i)

30


In [89]:
x = data.iloc[30]['X']
y = data.iloc[30]['Y']

In [90]:
data['X'] = data['X'] - x
data['Y'] = data['Y'] - y

In [121]:
m = folium.Map(location = [36.44,127.24],tiles='OpenStreetMap',zoom_start = 10)
for i,j,k,v in zip(data['lat'],data['lon'],data['X'],data['Y']):
    folium.CircleMarker([i,j],radius=1,popup='lat:{} lon:{}\nX:{} Y:{}'.format(i,j,k,v)
                        ,color='black',fill_color='black').add_to(m)
m

# Visualization
- 장치 포함

In [122]:
import json
import pandas as pd
import folium
file = 'tram/cctv.geojson'
geo = json.load(open(file,encoding='utf-8'))
cctv_df = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
cctv_df['lat'] = cctv_lat
cctv_df['lon'] = cctv_lon

for lat,lon in zip(cctv_df['lat'],cctv_df['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = 'cctv',
                        fill_color='yellow',
                        fill_opacity=0.7 ).add_to(m)

# 과주 방지 방치

file = 'tram/과주 방지 방치.geojson'
geo = json.load(open(file,encoding='utf-8'))
과주_방지_방치 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
과주_방지_방치['lat'] = cctv_lat
과주_방지_방치['lon'] = cctv_lon

for lat,lon in zip(과주_방지_방치['lat'],과주_방지_방치['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '과주_방지_방치',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 급전표시기

file = 'tram/급전표시기.geojson'
geo = json.load(open(file,encoding='utf-8'))
급전표시기 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
급전표시기['lat'] = cctv_lat
급전표시기['lon'] = cctv_lon

for lat,lon in zip(급전표시기['lat'],급전표시기['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '급전표시기',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 도로신호pole 

file = 'tram/도로신호pole.geojson'
geo = json.load(open(file,encoding='utf-8'))
도로신호pole = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
도로신호pole['lat'] = cctv_lat
도로신호pole['lon'] = cctv_lon

for lat,lon in zip(도로신호pole['lat'],도로신호pole['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '도로신호pole',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 분기기

file = 'tram/분기기.geojson'
geo = json.load(open(file,encoding='utf-8'))
분기기 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
분기기['lat'] = cctv_lat
분기기['lon'] = cctv_lon

for lat,lon in zip(분기기['lat'],분기기['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '분기기',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 선로전환기

file = 'tram/선로전환기.geojson'
geo = json.load(open(file,encoding='utf-8'))
선로전환기 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
선로전환기['lat'] = cctv_lat
선로전환기['lon'] = cctv_lon

for lat,lon in zip(선로전환기['lat'],선로전환기['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '선로전환기',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 신호등

file = 'tram/신호등.geojson'
geo = json.load(open(file,encoding='utf-8'))
신호등 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
신호등['lat'] = cctv_lat
신호등['lon'] = cctv_lon

for lat,lon in zip(신호등['lat'],신호등['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '신호등',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 신호제어기

file = 'tram/신호제어기.geojson'
geo = json.load(open(file,encoding='utf-8'))
신호제어기 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
신호제어기['lat'] = cctv_lat
신호제어기['lon'] = cctv_lon

for lat,lon in zip(신호제어기['lat'],신호제어기['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '신호제어기',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 안전거리 표지판

file = 'tram/안전거리 표지판.geojson'
geo = json.load(open(file,encoding='utf-8'))
안전거리_표지판 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
안전거리_표지판['lat'] = cctv_lat
안전거리_표지판['lon'] = cctv_lon

for lat,lon in zip(안전거리_표지판['lat'],안전거리_표지판['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '안전거리_표지판',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 전철주 지지대

file = 'tram/전철주 지지대.geojson'
geo = json.load(open(file,encoding='utf-8'))
전철주_지지대 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
전철주_지지대['lat'] = cctv_lat
전철주_지지대['lon'] = cctv_lon

for lat,lon in zip(전철주_지지대['lat'],전철주_지지대['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '전철주_지지대',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 전철주

file = 'tram/전철주.geojson'
geo = json.load(open(file,encoding='utf-8'))
전철주 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
전철주['lat'] = cctv_lat
전철주['lon'] = cctv_lon

for lat,lon in zip(전철주['lat'],전철주['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '전철주',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 접속함

file = 'tram/접속함.geojson'
geo = json.load(open(file,encoding='utf-8'))
접속함 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
접속함['lat'] = cctv_lat
접속함['lon'] = cctv_lon

for lat,lon in zip(접속함['lat'],접속함['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '접속함',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 제한속도 표지판

file = 'tram/제한속도 표지판.geojson'
geo = json.load(open(file,encoding='utf-8'))
제한속도_표지판 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
제한속도_표지판['lat'] = cctv_lat
제한속도_표지판['lon'] = cctv_lon

for lat,lon in zip(제한속도_표지판['lat'],제한속도_표지판['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '제한속도_표지판',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 진로 표시기

file = 'tram/진로 표시기.geojson'
geo = json.load(open(file,encoding='utf-8'))
진로_표시기 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
진로_표시기['lat'] = cctv_lat
진로_표시기['lon'] = cctv_lon

for lat,lon in zip(진로_표시기['lat'],진로_표시기['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '진로_표시기',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 차막이

file = 'tram/차막이.geojson'
geo = json.load(open(file,encoding='utf-8'))
차막이 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
차막이['lat'] = cctv_lat
차막이['lon'] = cctv_lon

for lat,lon in zip(차막이['lat'],차막이['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '차막이',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 트램 신호등

file = 'tram/트램 신호등.geojson'
geo = json.load(open(file,encoding='utf-8'))
트램_신호등 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
트램_신호등['lat'] = cctv_lat
트램_신호등['lon'] = cctv_lon

for lat,lon in zip(트램_신호등['lat'],트램_신호등['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '트램_신호등',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 트램 신호장치

file = 'tram/트램 신호장치.geojson'
geo = json.load(open(file,encoding='utf-8'))
트램_신호장치 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
트램_신호장치['lat'] = cctv_lat
트램_신호장치['lon'] = cctv_lon

for lat,lon in zip(트램_신호장치['lat'],트램_신호장치['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '트램_신호장치',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 트램 표지판

file = 'tram/트램 표지판.geojson'
geo = json.load(open(file,encoding='utf-8'))
트램_표지판 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
트램_표지판['lat'] = cctv_lat
트램_표지판['lon'] = cctv_lon

for lat,lon in zip(트램_표지판['lat'],트램_표지판['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '트램_표지판',
                        fill_color='yellow',
                        fill_opacity=0.7 ).add_to(m)

# 횡단보도 표지판

file = 'tram/횡단보도 표지판.geojson'
geo = json.load(open(file,encoding='utf-8'))
횡단보도_표지판 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
횡단보도_표지판['lat'] = cctv_lat
횡단보도_표지판['lon'] = cctv_lon

for lat,lon in zip(횡단보도_표지판['lat'],횡단보도_표지판['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '횡단보도_표지판',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

# 횡단보도

file = 'tram/횡단보도.geojson'
geo = json.load(open(file,encoding='utf-8'))
횡단보도 = pd.DataFrame(columns=['lat','lon'])
cctv_lon = []
cctv_lat = []
for i in range(len(geo['features'])):
    cctv_lon.append(geo['features'][i]['geometry']['coordinates'][0])
    cctv_lat.append(geo['features'][i]['geometry']['coordinates'][1])
횡단보도['lat'] = cctv_lat
횡단보도['lon'] = cctv_lon

for lat,lon in zip(횡단보도['lat'],횡단보도['lon']):
    folium.CircleMarker([lat,lon],radius=2,
                        color='yellow',
                         popup = '횡단보도',
                        fill_color='green',
                        fill_opacity=0.7 ).add_to(m)

In [123]:
m

In [98]:
# data.to_excel('geo_final/sub_final.xlsx',index=False)

In [109]:
for i in os.listdir('geo_final/')[2:]:
    df = pd.read_excel('geo_final/{}'.format(i))
    df['new_X'] = df['X'] - x
    df['new_Y'] = df['Y'] - y
    df.to_excel('geo_final/{}'.format(i),index=False)

In [112]:
start = pd.read_excel('geo_final/x1_points.xlsx')
line =  pd.read_excel('geo_final/x1_x2.xlsx')
line2 = pd.read_excel('geo_final/x2_straight_points.xlsx')
line3 = pd.read_excel('geo_final/x2-x3.xlsx')
end = pd.read_excel('geo_final/x3_final.xlsx')

In [114]:
main_line = pd.concat([start,line,line2,line3,end]).reset_index(drop=True)
main_line

lat         lon             X             Y        new_X  \
0     36.638751  127.305672  6.086364e+06  4.651085e+06     0.000000   
1     36.638756  127.305682  6.086364e+06  4.651087e+06     0.083579   
2     36.638760  127.305691  6.086364e+06  4.651088e+06     0.167157   
3     36.638765  127.305701  6.086364e+06  4.651090e+06     0.250736   
4     36.638770  127.305710  6.086364e+06  4.651092e+06     0.334316   
...         ...         ...           ...           ...          ...   
1341  36.630040  127.315749  6.085004e+06  4.652759e+06 -1359.399609   
1342  36.630033  127.315756  6.085003e+06  4.652760e+06 -1360.432584   
1343  36.630026  127.315764  6.085002e+06  4.652761e+06 -1361.465560   
1344  36.630020  127.315771  6.085001e+06  4.652763e+06 -1362.498537   
1345  36.630013  127.315778  6.085000e+06  4.652764e+06 -1363.531514   

            new_Y  
0        0.000000  
1        1.704496  
2        3.408993  
3        5.113490  
4        6.817988  
...           ...  
1341  1673.878265  
1342  1675.117051  
1343  1676.355837  
1344  1677.594624  
1345  1678.833411  

[1346 rows x 6 columns]

In [115]:
dis = []
for i in range(len(main_line)):
    if i == 0:
        dis.append(0)
    else:
        calculator(main_line['lat'][i])

1346

In [116]:
dis = []
for i in range(len(main_line)-1):
    if i == 0:
        dis.append(np.nan)
    x1 = main_line['lat'][i]
    y1 = main_line['lon'][i]
    x2 = main_line['lat'][i+1]
    y2 = main_line['lon'][i+1]
    cal=calculator(x1,x2,y1,y2)
    dis.append(cal.distance())
    ang.append(cal.bearing())
main_line['distance'] = dis
main_line.fillna(0,inplace=True)
main_line

lat         lon             X             Y        new_X  \
0     36.638751  127.305672  6.086364e+06  4.651085e+06     0.000000   
1     36.638756  127.305682  6.086364e+06  4.651087e+06     0.083579   
2     36.638760  127.305691  6.086364e+06  4.651088e+06     0.167157   
3     36.638765  127.305701  6.086364e+06  4.651090e+06     0.250736   
4     36.638770  127.305710  6.086364e+06  4.651092e+06     0.334316   
...         ...         ...           ...           ...          ...   
1341  36.630040  127.315749  6.085004e+06  4.652759e+06 -1359.399609   
1342  36.630033  127.315756  6.085003e+06  4.652760e+06 -1360.432584   
1343  36.630026  127.315764  6.085002e+06  4.652761e+06 -1361.465560   
1344  36.630020  127.315771  6.085001e+06  4.652763e+06 -1362.498537   
1345  36.630013  127.315778  6.085000e+06  4.652764e+06 -1363.531514   

            new_Y  distance  
0        0.000000       0.0  
1        1.704496       1.0  
2        3.408993       1.0  
3        5.113490       1.0  
4        6.817988       1.0  
...           ...       ...  
1341  1673.878265       1.0  
1342  1675.117051       1.0  
1343  1676.355837       1.0  
1344  1677.594624       1.0  
1345  1678.833411       1.0  

[1346 rows x 7 columns]

In [118]:
sub_start = pd.read_excel('geo_final/sub_start.xlsx')
dis = []
for i in range(len(sub_start)-1):
    if i == 0:
        dis.append(np.nan)
    x1 = sub_start['lat'][i]
    y1 = sub_start['lon'][i]
    x2 = sub_start['lat'][i+1]
    y2 = sub_start['lon'][i+1]
    cal=calculator(x1,x2,y1,y2)
    dis.append(cal.distance())
sub_start['distance'] = dis
sub_start.fillna(0,inplace=True)
sub_start

lat         lon             X             Y      new_X      new_Y  \
0   36.638698  127.305852  6.086350e+06  4.651116e+06 -13.462337  30.883444   
1   36.638701  127.305862  6.086350e+06  4.651118e+06 -13.519667  32.698152   
2   36.638705  127.305873  6.086350e+06  4.651120e+06 -13.576998  34.512862   
3   36.638709  127.305883  6.086350e+06  4.651121e+06 -13.634328  36.327572   
4   36.638712  127.305893  6.086350e+06  4.651123e+06 -13.691658  38.142282   
5   36.638716  127.305903  6.086350e+06  4.651125e+06 -13.748988  39.956994   
6   36.638719  127.305914  6.086350e+06  4.651127e+06 -13.861192  41.806229   
7   36.638722  127.305924  6.086350e+06  4.651129e+06 -13.973396  43.655465   
8   36.638726  127.305935  6.086349e+06  4.651131e+06 -14.085600  45.504702   
9   36.638729  127.305945  6.086349e+06  4.651132e+06 -14.197804  47.353939   
10  36.638730  127.305956  6.086349e+06  4.651134e+06 -14.503317  49.286002   
11  36.638732  127.305967  6.086349e+06  4.651136e+06 -14.808829  51.218066   
12  36.638734  127.305978  6.086348e+06  4.651138e+06 -15.114342  53.150131   
13  36.638734  127.305989  6.086348e+06  4.651140e+06 -15.616250  55.097613   
14  36.638733  127.306001  6.086347e+06  4.651142e+06 -16.118159  57.045096   
15  36.638733  127.306012  6.086347e+06  4.651144e+06 -16.620068  58.992580   
16  36.638733  127.306023  6.086346e+06  4.651146e+06 -17.121978  60.940065   
17  36.638732  127.306034  6.086346e+06  4.651148e+06 -17.711309  62.867569   
18  36.638731  127.306045  6.086345e+06  4.651150e+06 -18.300641  64.795074   
19  36.638730  127.306056  6.086345e+06  4.651152e+06 -18.889973  66.722580   
20  36.638729  127.306067  6.086344e+06  4.651154e+06 -19.479306  68.650087   
21  36.638727  127.306078  6.086343e+06  4.651156e+06 -20.193849  70.511690   
22  36.638724  127.306089  6.086343e+06  4.651157e+06 -20.908391  72.373294   
23  36.638722  127.306100  6.086342e+06  4.651159e+06 -21.622935  74.234898   
24  36.638720  127.306111  6.086341e+06  4.651161e+06 -22.337479  76.096503   
25  36.638716  127.306121  6.086340e+06  4.651163e+06 -23.182039  77.824019   
26  36.638712  127.306131  6.086340e+06  4.651165e+06 -24.026599  79.551535   
27  36.638708  127.306141  6.086339e+06  4.651166e+06 -24.871160  81.279052   
28  36.638704  127.306151  6.086338e+06  4.651168e+06 -25.715722  83.006569   
29  36.638701  127.306161  6.086337e+06  4.651170e+06 -26.560285  84.734087   

    distance  
0        0.0  
1        1.0  
2        1.0  
3        1.0  
4        1.0  
5        1.0  
6        1.0  
7        1.0  
8        1.0  
9        1.0  
10       1.0  
11       1.0  
12       1.0  
13       1.0  
14       1.0  
15       1.0  
16       1.0  
17       1.0  
18       1.0  
19       1.0  
20       1.0  
21       1.0  
22       1.0  
23       1.0  
24       1.0  
25       1.0  
26       1.0  
27       1.0  
28       1.0  
29       1.0

In [119]:
x2_curve = pd.read_excel('geo_final/x2_curve.xlsx')
dis = []
for i in range(len(x2_curve)-1):
    if i == 0:
        dis.append(np.nan)
    x1 = x2_curve['lat'][i]
    y1 = x2_curve['lon'][i]
    x2 = x2_curve['lat'][i+1]
    y2 = x2_curve['lon'][i+1]
    cal=calculator(x1,x2,y1,y2)
    dis.append(cal.distance())
x2_curve['distance'] = dis
x2_curve.fillna(0,inplace=True)
x2_curve

lat         lon             X             Y       new_X  \
0    36.633529  127.311914  6.085540e+06  4.652123e+06 -823.516033   
1    36.633521  127.311919  6.085539e+06  4.652124e+06 -824.583494   
2    36.633513  127.311925  6.085538e+06  4.652125e+06 -825.650956   
3    36.633505  127.311930  6.085537e+06  4.652126e+06 -826.718418   
4    36.633497  127.311935  6.085536e+06  4.652127e+06 -827.785881   
..         ...         ...           ...           ...         ...   
160  36.632456  127.313098  6.085375e+06  4.652320e+06 -988.488521   
161  36.632451  127.313107  6.085374e+06  4.652321e+06 -989.395675   
162  36.632446  127.313117  6.085373e+06  4.652323e+06 -990.302830   
163  36.632442  127.313126  6.085372e+06  4.652325e+06 -991.209986   
164  36.632437  127.313136  6.085371e+06  4.652326e+06 -992.117144   

           new_Y  distance  
0    1038.380462       0.0  
1    1039.238979       1.0  
2    1040.097497       1.0  
3    1040.956015       1.0  
4    1041.814532       1.0  
..           ...       ...  
160  1234.585830       1.0  
161  1236.212895       1.0  
162  1237.839960       1.0  
163  1239.467026       1.0  
164  1241.094092       1.0  

[165 rows x 7 columns]

In [120]:
# with pd.ExcelWriter('geo_final/final.xlsx') as writer:
#     main_line.to_excel(writer,sheet_name = 'main')
#     sub_start.to_excel(writer,sheet_name = 'sub_start')
#     x2_curve.to_excel(writer,sheet_name = 'divide_point')

# 실제 좌표 추가 visualization

In [125]:
import folium
for lat, lon,idx in zip(point['latitude'], point['longitude'],range(len(point))):
    folium.CircleMarker([lat, lon],
                        radius=2,
                        color='red',
                        popup = '{},{}'.format(lat,lon),
                        fill_color='red',
                        fill_opacity=0.7 ).add_to(m)

In [127]:
m.save('geo_final/final.html')